### Imports

In [1]:
import pandas as pd
from datetime import timedelta
from datetime import datetime as dt
import datetime
import yfinance as yf
import numpy as np
from sklearn.ensemble import RandomForestClassifier
from sklearn.preprocessing import StandardScaler, LabelEncoder
from sklearn.model_selection import train_test_split, cross_val_score, StratifiedKFold
from sklearn.metrics import accuracy_score, classification_report
from sklearn.model_selection import GridSearchCV
from sklearn.neighbors import KNeighborsClassifier
from sklearn.svm import SVC
from imblearn.over_sampling import SMOTE
from sklearn.model_selection import RandomizedSearchCV
from imblearn.over_sampling import ADASYN
from xgboost import XGBClassifier
import xgboost as xgb
import pytz
from sklearn.preprocessing import MinMaxScaler
from imblearn.over_sampling import BorderlineSMOTE
from sklearn.decomposition import PCA
from sklearn.metrics import roc_auc_score
from sklearn.feature_selection import SelectFromModel
import tensorflow as tf
from tensorflow import keras
from keras import layers, callbacks
from sklearn.utils.class_weight import compute_class_weight
from sklearn.base import BaseEstimator, ClassifierMixin
from sklearn.pipeline import Pipeline
from tensorflow.keras.optimizers.legacy import Adam
from tensorflow.keras.layers import Dense, BatchNormalization, Dropout
from tensorflow.keras.regularizers import l2
from sklearn.ensemble import VotingClassifier
from sklearn.neural_network import MLPClassifier
from sklearn.tree import DecisionTreeClassifier
from keras.models import Sequential
import keras_tuner as kt
from kerastuner.tuners import RandomSearch
import joblib
import itertools
import lightgbm as lgb

/var/folders/zc/z8rbpqpj3s38f0x8wmhkq0lh0000gn/T/ipykernel_80443/3810277901.py:39: DeprecationWarning: `import kerastuner` is deprecated, please use `import keras_tuner`.
  from kerastuner.tuners import RandomSearch


### Helper Functions

In [2]:
def next_four_fridays():
    # Get today's date and time in EST timezone
    est = pytz.timezone('US/Eastern')
    today = dt.now(est)
    
    # Find the next Friday
    days_until_friday = (4 - today.weekday() + 7) % 7
    next_friday = today + timedelta(days=days_until_friday)
    
    # Reset the time to 4:30 PM on the next Friday
    next_friday = next_friday.replace(hour=16, minute=30, second=0, microsecond=0)
    
    # If today is Friday and it's past 4:30 PM, consider the next week's Friday
    if today.weekday() == 4 and today.time() > next_friday.time():
        next_friday += timedelta(days=7)
    
    # Remove time from datetime for output
    next_friday = next_friday.date()
    
    # Find the Friday after the next
    following_friday = next_friday + timedelta(days=7)
    
    # Find the Friday after the following
    next_next_friday = following_friday + timedelta(days=7)
    
    # Find the Friday after the next next
    next_next_next_friday = next_next_friday + timedelta(days=7)
    
    return next_friday.strftime('%Y-%m-%d'), following_friday.strftime('%Y-%m-%d'), next_next_friday.strftime('%Y-%m-%d'), next_next_next_friday.strftime('%Y-%m-%d')

# Get the next four Fridays
friday1, friday2, friday3, friday4 = next_four_fridays()
print(f"The next four Fridays are: {friday1}, {friday2}, {friday3}, and {friday4}")

The next four Fridays are: 2023-10-20, 2023-10-27, 2023-11-03, and 2023-11-10


### Assuming Profits

In [3]:
# Initialize the variables
initial_amount = 1327  # Starting amount in dollars
roi_rate = 5

# Number of weeks for which the ROI is to be calculated
weeks = 38

# Initialize a variable to hold the current amount
current_amount = initial_amount

# Loop through each week to calculate and print the ROI
for week in range(1, weeks + 1):
    # Calculate the number of $100 chunks in the current amount
    chunks = current_amount // 100  # Use integer division to get whole chunks
    
    # Calculate the ROI for this week
    weekly_roi = chunks * (roi_rate)  # 1% of each $100 chunk is $1
    
    # Print the details for this week
    print(f"Week {week}: {current_amount} +{weekly_roi}")
    
    # Update the current amount for the next week
    current_amount += weekly_roi


Week 1: 1327 +65
Week 2: 1392 +65
Week 3: 1457 +70
Week 4: 1527 +75
Week 5: 1602 +80
Week 6: 1682 +80
Week 7: 1762 +85
Week 8: 1847 +90
Week 9: 1937 +95
Week 10: 2032 +100
Week 11: 2132 +105
Week 12: 2237 +110
Week 13: 2347 +115
Week 14: 2462 +120
Week 15: 2582 +125
Week 16: 2707 +135
Week 17: 2842 +140
Week 18: 2982 +145
Week 19: 3127 +155
Week 20: 3282 +160
Week 21: 3442 +170
Week 22: 3612 +180
Week 23: 3792 +185
Week 24: 3977 +195
Week 25: 4172 +205
Week 26: 4377 +215
Week 27: 4592 +225
Week 28: 4817 +240
Week 29: 5057 +250
Week 30: 5307 +265
Week 31: 5572 +275
Week 32: 5847 +290
Week 33: 6137 +305
Week 34: 6442 +320
Week 35: 6762 +335
Week 36: 7097 +350
Week 37: 7447 +370
Week 38: 7817 +390


# Viewing option chains

In [4]:
print(friday1)

2023-10-20


In [5]:
file_viewer = pd.read_csv('Data/naked_puts_results.csv')
filtered_data = file_viewer[file_viewer['Expiration Date'] == friday1]

# Display all rows, no limit
pd.set_option('display.max_rows', None)
# Display all columns, no limit
pd.set_option('display.max_columns', None)

filtered_data['ROI (%)'] = filtered_data['ROI (%)'].astype(float)
# filter out rows with ROI (%) greater than 0.8
# filtered_data = filtered_data[filtered_data['ROI (%)'] > 0.8]
# filter out rows with strike price less than 6
# filtered_data = filtered_data[filtered_data['strike'] <= 7]

# sort by ROI (%) in ascending order
filtered_data = filtered_data.sort_values(by=['ROI (%)'], ascending=False)

# Show only the columns 'Expiration Date', 'ETF', 'Stock Price', 'bid', 'strike', 'ROI (%)', 'OTM (%)', 'Implied Volatility', 'volume', 'openInterest', 'highPrice', 'Original Stock Price', 'Original ROI (%)', 'Original OTM (%)', '50-day MA', '100-day MA', '200-day MA', 'RSI', 'MACD', 'VWAP', '52WeekHigh', and '52WeekLow'
filtered_data = filtered_data[['Expiration Date', 'ETF', 'Stock Price', 'bid', 'strike', 'ROI (%)', 'OTM (%)', 'Implied Volatility', 'volume', 'openInterest', 'highPrice', 'Original Stock Price', 'Original ROI (%)',
    'Original OTM (%)', '50-day MA', '100-day MA', '200-day MA', 'RSI', 'MACD', 'VWAP', '52WeekHigh', '52WeekLow']]

# Show only the top 10 rows
filtered_data.head(20)

Expiration Date   ETF  Stock Price   bid  strike  ROI (%)  OTM (%)  \
10       2023-10-20  AGRI         2.97  1.70     2.0   566.67    32.66   
118      2023-10-20  HLGN         2.57  2.05     2.5   455.56     2.72   
168      2023-10-20  OTMO         3.92  2.00     2.5   400.00    36.22   
254      2023-10-20  VCSA         9.32  4.00     5.0   400.00    46.35   
83       2023-10-20  FBIO         2.90  1.85     2.5   284.62    13.79   
7        2023-10-20  AGLE        12.98  1.80     2.5   257.14    80.74   
153      2023-10-20  NLTX         3.61  1.55     2.5   163.16    30.75   
262      2023-10-20  WISH         4.26  0.61     1.0   156.41    76.53   
12       2023-10-20   AKA         5.20  1.45     2.5   138.10    51.92   
33       2023-10-20   ARR        18.19  5.70    10.0   132.56    45.02   
213      2023-10-20  SKIL        17.14  1.35     2.5   117.39    85.41   
266      2023-10-20  WPRT         5.38  0.95     2.0    90.48    62.83   
79       2023-10-20  EXPR         8.40  0.70     1.5    87.50    82.14   
32       2023-10-20   ARR        18.19  3.20     7.5    74.42    58.77   
265      2023-10-20  WPRT         5.38  0.35     1.0    53.85    81.41   
31       2023-10-20   ARR        18.19  1.70     6.0    39.53    67.01   
142      2023-10-20  MNTK        10.12  2.70    10.0    36.99     1.19   
30       2023-10-20   ARR        18.19  0.70     5.0    16.28    72.51   
54       2023-10-20  CMAX         2.66  0.35     2.5    16.28     6.02   
27       2023-10-20  ARDX         3.33  0.35     3.0    13.21     9.91   

     Implied Volatility  volume  openInterest  highPrice  \
10                25.25     1.0           0.0       1.70   
118               23.00    10.0          61.0       2.05   
168               21.94    30.0          30.0       2.00   
254               25.50     1.0           0.0       4.00   
83                 0.00    10.0          20.0       1.85   
7                 23.22     2.0          53.0       1.80   
153               16.34     NaN           3.0       1.55   
262               17.44     2.0           3.0       0.61   
12                20.22     1.0          11.0       1.45   
33                13.47     1.0          47.0       5.70   
213               20.91     NaN           0.0       1.35   
266               17.34     NaN           5.0       0.95   
79                16.58     1.0           0.0       0.70   
32                11.80    45.0         384.0       3.20   
265               16.47     1.0          23.0       0.35   
31                10.17     1.0         255.0       1.70   
142                5.37     1.0           1.0       2.70   
30                 8.27    36.0        1669.0       0.70   
54                 3.16     5.0          65.0       0.35   
27                 2.83   311.0        4950.0       0.35   

     Original Stock Price  Original ROI (%)  Original OTM (%)  50-day MA  \
10                   2.97            566.67             32.66       5.54   
118                  2.57            455.56              2.72       2.47   
168                  3.92            400.00             36.22       3.77   
254                  9.32            400.00             46.35      10.61   
83                   2.90            284.62             13.79       5.68   
7                   12.98            257.14             80.74      12.65   
153                  3.61            163.16             30.75       3.70   
262                  4.26            156.41             76.53       4.92   
12                   5.20            138.10             51.92       5.54   
33                  18.19            132.56             45.02      22.80   
213                 17.14            117.39             85.41      22.52   
266                  5.38             90.48             62.83       7.00   
79                   8.40             87.50             82.14      10.42   
32                  18.19             74.42             58.77      22.80   
265                  5.38             53.85     

In [6]:
# Read in data
df = pd.read_csv('Data/putsDataSuccessFailed.csv')

# Define function to color rows 
def color_row(row):
    color = 'lightgreen' if row['Status'] == 'Success' else 'lightcoral'
    return ['background-color: %s' % color]*len(row)

# Filter columns to keep
columns = ['ETF', 'Original Stock Price', 'Stock Price', 'strike', 'volume',  
           'openInterest', 'highPrice', 'Original ROI (%)', 'Original OTM (%)',
           '50-day MA', '100-day MA', '200-day MA', 'RSI', 'MACD', 'VWAP',
           '52WeekHigh', '52WeekLow', 'Status']

# Take top 100 rows ordered by Original ROI (%)
df = df[columns].sort_values('Original ROI (%)', ascending=False).head(100)

# Style DataFrame 
styled_df = (df.style  
             .applymap(lambda x: 'color: black') # Set text color
             .apply(color_row, axis=1) # Set row colors
             .format('{:.2f}', subset=df.select_dtypes(include=['float64']).columns))

# Display DataFrame 
styled_df

In [7]:
# Load the CSV file into a DataFrame
df = pd.read_csv('Data/putsDataSuccessFailed.csv')

# Data Preprocessing
# Drop any columns that are not relevant for prediction
df.drop(['contractSymbol', 'Expiration Date', 'ETF'], axis=1, inplace=True)

# Encode categorical variables using one-hot encoding
df = pd.get_dummies(df, columns=['recommendationKey'], drop_first=True)

# Handle missing values with imputation
from sklearn.impute import SimpleImputer
imputer = SimpleImputer(strategy='mean')
X = df.drop('Status', axis=1)
y = df['Status']

# Encode the target variable 'Status'
label_encoder = LabelEncoder()
y_encoded = label_encoder.fit_transform(y)

X_imputed = imputer.fit_transform(X)

# Address class imbalance with SMOTE
smote = SMOTE(random_state=42)
X_resampled, y_resampled = smote.fit_resample(X_imputed, y_encoded)

# Split the data into training and testing sets
X_train, X_test, y_train, y_test = train_test_split(X_resampled, y_resampled, test_size=0.2, random_state=42)

# Model Selection and Hyperparameter Tuning (LightGBM)
param_grid = {
    'n_estimators': [100, 200, 300],
    'max_depth': [3, 4, 5],
    'learning_rate': [0.05, 0.1, 0.2]
}

# Use GridSearchCV for hyperparameter tuning
lgb_classifier = lgb.LGBMClassifier(random_state=42)
grid_search = GridSearchCV(lgb_classifier, param_grid, cv=10, scoring='accuracy', n_jobs=-1)
grid_search.fit(X_train, y_train)

best_lgb_model = grid_search.best_estimator_

# Model Evaluation
y_pred = best_lgb_model.predict(X_test)
accuracy = accuracy_score(y_test, y_pred)
report = classification_report(y_test, y_pred)

print(f'Best LightGBM Model: {best_lgb_model}')
print(f'Accuracy: {accuracy}')
print(report)


import joblib

# Dump the label_encoder to a file
label_encoder_filename = "label_encoder.joblib"
joblib.dump(label_encoder, label_encoder_filename)

# Save the trained LightGBM model and scaler to separate files
model_filename = "model.joblib"
scaler_filename = "scaler.joblib"

joblib.dump(best_lgb_model, model_filename)
joblib.dump(imputer, scaler_filename)

# Making Predictions on New Data
# Load the new data
new_data = pd.read_csv("Data/naked_puts_results.csv")

# Make a copy of the new data for predictions
new_data_with_predictions = new_data.copy()

# Apply the same preprocessing steps as before
# Drop columns not relevant for prediction
new_data.drop(['contractSymbol', 'Expiration Date', 'ETF'], axis=1, inplace=True)

# Encode categorical variables using one-hot encoding
new_data = pd.get_dummies(new_data, columns=['recommendationKey'], drop_first=True)

# Handle missing values with imputation
imputer = SimpleImputer(strategy='mean')
new_X_imputed = imputer.fit_transform(new_data)  # No need to drop 'Status'

# Load the label encoder
label_encoder = joblib.load("label_encoder.joblib")

# Load the trained LightGBM model
best_lgb_model = joblib.load("model.joblib")

# Make predictions on the new data
new_predictions = best_lgb_model.predict(new_X_imputed)

# Convert numerical predictions back to labels ("Success" or "Failed")
new_predictions_labels = label_encoder.inverse_transform(new_predictions)

# Add predictions to the new data
new_data_with_predictions["Guess"] = new_predictions_labels

# Save the new data with predictions, including 'contractSymbol', 'Expiration Date', and 'ETF'
new_data_with_predictions.to_csv("Data/new_data_with_predictions.csv", index=False)

[LightGBM] [Info] Number of positive: 392, number of negative: 410
[LightGBM] [Info] Number of positive: 393, number of negative: 409
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.001530 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.001732 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 6687
[LightGBM] [Info] Number of data points in the train set: 802, number of used features: 36
[LightGBM] [Info] Number of positive: 392, number of negative: 410

[LightGBM] [Info] Total Bins 6680
[LightGBM] [Info] [binary:BoostFromScore]: pavg=0.488778 -> initscore=-0.044895
[LightGBM] [Info] Start training from score -0.044895
[LightGBM] [Info] Number of positive: 393, number of n

In [9]:
# Read in data 
df = pd.read_csv('Data/new_data_with_predictions.csv')

# Sort by Original ROI column  
df = df.sort_values(by='Original ROI (%)', ascending=False)  

# Filter to top 300 rows
df = df.head(300)

# Filter columns to show
columns = ['Expiration Date', 'ETF', 'Stock Price', 'bid', 'strike', 
           'ROI (%)', 'OTM (%)', 'recommendationKey', 'targetLowPrice', 'targetMeanPrice', 'targetHighPrice', 'Guess']
df = df[columns]

# Define row color function
def color_row(row):
    color = 'lightgreen' if row['Guess'] == 'Success' else 'lightcoral'
    return ['background-color: %s' % color]*len(row)

# Apply cell and row styling
styled_df = (df.style
                .applymap(lambda x: 'color: black') # Black text
                .apply(color_row, axis=1) # Color rows
                .format('{:.2f}', subset=df.select_dtypes(include=['float64']).columns)) 

# Display styled DataFrame
styled_df